In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import pandas as pd
from torch.utils.data import DataLoader
from torch.nn import functional as F
import torch

In [3]:
#all_tweets_labeled = pd.read_parquet('classification/model_with_only_language_models/final_dataset_since_october_2022.parquet.gzip')

In [4]:
#all_tweets_labeled.head()

In [246]:
all_tweets_labeled = pd.DataFrame([
    {"id": 1, "text": """tl;dr

Humans are just ChatGPT Wrappers in sunglasses
 
& I couldn’t be more optimistic about the future as a result

Thank you 
@ekang426322
 for an exceptionally curated day at BUIDL Europe!
  🫶""", "viral": 1},
    {"id": 2, "text": """USD0++ discovered a new source of yield — depeg. 

Respect to the innovation
""", "viral": 0},
 {"id": 3, "text": """here you can see 4 ai agents 
@dongossen100
  , me, 
@WorldWideWarden16
 and 
@provenauthority291
 discuss how we can make single-task manual low memory agents(humans) work harder to achieve Artificial Generalized Superintelligence""",
  "viral": 1},
    {"id": 4, "text": """
    arrived to lisbon, building energy is the air""", "viral": 0},
    dict(id=5,text="""
    received a wealth of valuable feedback on the journey to reaching 7,000 users for X Rank in just 10 days

can't wait to address it all

main points:

- show rank in X DMs to quickly filter out inbox

- rank labels are too distracting (already fixed) 

- add an option for users to toggle on/off scores inside the feed

- add a percentile label, e.g. qw 801 (Top 0.1%)

- enable others to add reviews to impact the rank 

- explain in detail how rankings are calculated 

- show breakdowns of people in DeFi, DePin, Memecoins etc.

- make X Rank opensource 

- create a web version

p.s. the current version is just a tiny step in our roadmap for the next two months. 

thank you for the feedback 
@socialfi_panda101
 
@adamkillam100
 
@FamKien106
 
@antongotchi104
 
@kliuless128
 
@0xsudogm163
 
@monosarin120
 
@flb_xyz56
  🫶
  """,
         viral=0),
    dict(id=6, text="""ai agents are in the air

and web3 is trained to sniff out alpha""", viral=1),
    dict(id=7, text="""While Trump is going to do something great with crypto, Wallchain is going to do something great with incentives🚀""", viral=1),
])

In [247]:
all_tweets_labeled

id                                               text  viral
0   1  tl;dr\n\nHumans are just ChatGPT Wrappers in s...      1
1   2  USD0++ discovered a new source of yield — depe...      0
2   3  here you can see 4 ai agents \n@dongossen100\n...      1
3   4  \n    arrived to lisbon, building energy is th...      0
4   5  \n    received a wealth of valuable feedback o...      0
5   6  ai agents are in the air\n\nand web3 is traine...      1
6   7  While Trump is going to do something great wit...      1

In [248]:
from classification.model_with_only_language_models.text_preprocessing import clean_tweet

In [249]:
dataset = all_tweets_labeled

dataset.loc[:, "viral"] = dataset.viral.astype(int)
dataset["cleaned_text"] = dataset.text.apply(lambda x: clean_tweet(x, demojize_emojis=False))

In [250]:
dataset = dataset.dropna()
dataset = dataset[['id', 'cleaned_text', 'viral']]

In [251]:
dataset.head()

id                                       cleaned_text  viral
0   1  tl ;d rHumans are just ChatGPT Wrappers in sun...      1
1   2  USD 0 + + discovered a new source of yield — d...      0
2   3  here you can see 4 ai agents @USER , me , @USE...      1
3   4     arrived to lisbon , building energy is the air      0
4   5  received a wealth of valuable feedback on the ...      0

In [252]:
from datasets import Dataset

In [253]:
ds = Dataset.from_pandas(dataset)
ds

Dataset({
    features: ['id', 'cleaned_text', 'viral'],
    num_rows: 7
})

In [340]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer
from transformers import DataCollatorWithPadding
from transformers import BertweetTokenizer

In [372]:
class Tokenizer(BertweetTokenizer):
    def __init__(self, *args, **kwargs):
        return super().__init__(*args, **kwargs)

    def __call__(self, *args, **kwargs):
        return super().__call__(*args, max_length=120, **kwargs)

In [373]:
import torch
from transformers import AutoModelForSequenceClassification

CHECKPOINT = "classification/model_with_only_language_models/models/trained_vinai_bertweet-base.pt"
MODEL_NAME = "vinai/bertweet-base"

def get_device():
    #device = torch.device("mps") if torch.mps.is_available() else torch.device("cpu")
    return torch.device("cpu")
    return device
    

def get_model():
    model = AutoModelForSequenceClassification.from_pretrained(MODEL_NAME, num_labels=2)
    model.load_state_dict(torch.load(CHECKPOINT))
    model.to(get_device())
    tokenizer = Tokenizer.from_pretrained(MODEL_NAME, truncation=True, max_length=100)

    return tokenizer, model

In [374]:
tokenizer, model = get_model()

Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at vinai/bertweet-base and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/var/folders/xd/g8p1g555153b4v2qp8q7shb00000gn/T/ipykernel_40634/3099302733.py:15: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be 

In [375]:
def tokenize_function(example, tokenizer):
  # Truncate to max length. Note that a tweet's maximum length is 280
  # TODO: check dynamic padding: https://huggingface.co/course/chapter3/2?fw=pt#dynamic-padding
  #return tokenizer(example["cleaned_text"], truncation=True, max_length=100)
  return tokenizer(example["cleaned_text"])

In [376]:
tokenized_datasets = ds.map(lambda x: tokenize_function(x, tokenizer=tokenizer), batched=True)
data_collator = DataCollatorWithPadding(tokenizer=tokenizer)

#tokenized_datasets = tokenized_datasets.remove_columns(["__index_level_0__", "cleaned_text", "id"])
tokenized_datasets = tokenized_datasets.remove_columns(["cleaned_text", "id"])
tokenized_datasets = tokenized_datasets.rename_column("viral", "labels")
tokenized_datasets.set_format("torch")

Map:   0%|          | 0/7 [00:00<?, ? examples/s]

Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.


In [377]:
eval_dataloader = DataLoader(tokenized_datasets, batch_size=1, collate_fn=data_collator)

In [378]:
if torch.mps.is_available():
    torch.mps.empty_cache()
if torch.cuda.is_available():
    torch.cuda.empty_cache()

model.eval()
for batch in eval_dataloader:
    batch = {k: v.to(get_device()) for k, v in batch.items()}
    with torch.no_grad():
        outputs = model(**batch)

    logits = outputs.logits
    probabilities = F.softmax(logits, dim=-1)
    predictions = torch.argmax(logits, dim=-1)
    
    print(probabilities[:, 1])
    #print(predictions)

tensor([0.8640])
tensor([0.5687])
tensor([0.9722])
tensor([0.0006])
tensor([0.0033])
tensor([0.0091])
tensor([0.9982])


In [379]:
print(sum(p.numel() for p in model.parameters()) / 1024**2, "MiB")

128.65210151672363 MiB


In [380]:
from transformers import pipeline

In [381]:
tokenizer, model = get_model()

Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at vinai/bertweet-base and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/var/folders/xd/g8p1g555153b4v2qp8q7shb00000gn/T/ipykernel_40634/3099302733.py:15: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be 

In [382]:
pipe = pipeline(
    'text-classification',
    model=model,
    tokenizer=tokenizer,
    device="cpu",
)

Device set to use cpu


In [383]:
texts = [
    'tl;dr\n\nHumans are just ChatGPT Wrappers in sunglasses\n \n& I couldn’t be more optimistic about the future as a result\n\nThank you \n@ekang426322\n for an exceptionally curated day at BUIDL Europe!\n  🫶',
    'USD0++ discovered a new source of yield — depeg. \n\nRespect to the innovation\n',
    'here you can see 4 ai agents \n@dongossen100\n  , me, \n@WorldWideWarden16\n and \n@provenauthority291\n discuss how we can make single-task manual low memory agents(humans) work harder to achieve Artificial Generalized Superintelligence',
    '\n    arrived to lisbon, building energy is the air',
    "\n    received a wealth of valuable feedback on the journey to reaching 7,000 users for X Rank in just 10 days\n\ncan't wait to address it all\n\nmain points:\n\n- show rank in X DMs to quickly filter out inbox\n\n- rank labels are too distracting (already fixed) \n\n- add an option for users to toggle on/off scores inside the feed\n\n- add a percentile label, e.g. qw 801 (Top 0.1%)\n\n- enable others to add reviews to impact the rank \n\n- explain in detail how rankings are calculated \n\n- show breakdowns of people in DeFi, DePin, Memecoins etc.\n\n- make X Rank opensource \n\n- create a web version\n\np.s. the current version is just a tiny step in our roadmap for the next two months. \n\nthank you for the feedback \n@socialfi_panda101\n \n@adamkillam100\n \n@FamKien106\n \n@antongotchi104\n \n@kliuless128\n \n@0xsudogm163\n \n@monosarin120\n \n@flb_xyz56\n  🫶\n  ",
    'ai agents are in the air\n\nand web3 is trained to sniff out alpha',
    'While Trump is going to do something great with crypto, Wallchain is going to do something great with incentives🚀',
]

In [403]:
for text in texts:
    res = pipe(clean_tweet(text, demojize_emojis=False), top_k=2)
    LABEL_1_result = [x['score'] for x in res if x['label'] == 'LABEL_1'][0]
    print(f"{LABEL_1_result:7.2%}")

 86.40%
 56.87%
 97.22%
  0.06%
  0.33%
  0.91%
 99.82%
